In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline
import torch
import sys, os
import pystk
import ray
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
print('device = ', device)
ray.init(logging_level=50)

device =  cpu


{'node_ip_address': '127.0.0.1',
 'raylet_ip_address': '127.0.0.1',
 'redis_address': None,
 'object_store_address': '/tmp/ray/session_2022-04-14_13-48-32_722399_14551/sockets/plasma_store',
 'raylet_socket_name': '/tmp/ray/session_2022-04-14_13-48-32_722399_14551/sockets/raylet',
 'webui_url': None,
 'session_dir': '/tmp/ray/session_2022-04-14_13-48-32_722399_14551',
 'metrics_export_port': 56806,
 'gcs_address': '127.0.0.1:56833',
 'address': '127.0.0.1:56833',
 'node_id': 'eb28755e3f6b159424fdfa87b049657bbeb35e0193943700b8f7ce22'}

In [5]:
from utils.actors import new_action_net, Actor, GreedyActor
from utils.utils import show_agent, rollout_many
import numpy as np

In [13]:
action_net = new_action_net()
show_agent(Actor(action_net))

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (400, 300) to (400, 304) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).


In [16]:
many_action_nets = [new_action_net() for i in range(100)]

data = rollout_many([Actor(action_net) for action_net in many_action_nets], n_steps=600)

good_initialization = many_action_nets[ np.argmax([d[-1]['kart_info'].overall_distance for d in data]) ]

In [17]:
show_agent(Actor(good_initialization))

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (400, 300) to (400, 304) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).


Recall what we're trying to do in RL: maximize the expected return of a policy $\pi$ (or in turn minmize a los $L$)
$$
-L = E_{\tau \sim P_\pi}[R(\tau)],
$$
where $\tau = \{s_0, a_0, s_1, a_1, \ldots\}$ is a trajectory of states and actions.
The return of a trajectory is then defined as the sum of individual rewards $R(\tau) = \sum_k r(s_k)$ (we won't discount in this assignment).

Policy gradient computes the gradient of the loss $L$ using the log-derivative trick
$$
\nabla_\pi L = -E_{\tau \sim P_\pi}[\sum_k r(s_k) \nabla_\pi \sum_i \log \pi(a_i | s_i)].
$$
Since the return $r(s_k)$ only depends on action $a_i$ in the past $i < k$ we can further simplify the above equation:
$$
\nabla_\pi L = -E_{\tau \sim P_\pi}\left[\sum_i \left(\nabla_\pi \log \pi(a_i | s_i)\right)\left(\sum_{k=i}^{i+T} r(s_k) \right)\right].
$$
We will implement an estimator for this objective below. There are a few steps that we need to follow:

 * The expectation $E_{\tau \sim P_\pi}$ are rollouts of our policy
 * The log probability $\log \pi(a_i | s_i)$ uses the `Categorical.log_prob`
 * Gradient computation uses the `.backward()` function
 * The gradient $\nabla_\pi L$ is then used in a standard optimizer

In [18]:
from utils.reinforce import reinforce
import copy

action_net = copy.deepcopy(good_initialization)

best_action_net = reinforce(action_net, n_epochs=3, n_trajectories=400)

tensor([ 9.4092e+02,  9.4092e+02,  7.1951e+01,  ..., -1.0719e-02,
         5.4474e-03,  0.0000e+00])
epoch = 0   best_dist =  359.1201477050781
tensor([646.3047, 646.3047, 156.4215,  ...,  17.7727,   8.3517,   0.0000])
epoch = 1   best_dist =  946.6754150390625
tensor([917.9937, 919.6048, 115.3470,  ...,   0.0000,   0.0000,   0.0000])
epoch = 2   best_dist =  946.6754150390625


In [19]:
show_agent(GreedyActor(best_action_net))

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (400, 300) to (400, 304) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).


In [ ]:
best_action_net=lateral_net